In [6]:
#!pip install avalanche-lib==0.3.1
#!pip install torcheval
!pip install numba

Looking in indexes: https://pypi.org/simple, https://packagecloud.io/github/git-lfs/pypi/simple
  Using cached numpy-1.21.6-cp39-cp39-manylinux_2_12_x86_64.manylinux2010_x86_64.whl (15.7 MB)
  Attempting uninstall: numpy
    Found existing installation: numpy 1.22.0
    Uninstalling numpy-1.22.0:
      Successfully uninstalled numpy-1.22.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
daal4py 2021.6.0 requires daal==2021.4.0, which is not installed.
darts 0.27.1 requires pytorch-lightning>=1.5.0, which is not installed.
bokeh 2.4.3 requires typing-extensions>=3.10.0, but you have typing-extensions 3.7.4.3 which is incompatible.
torchtext 0.10.1 requires torch==1.9.1, but you have torch 1.12.1+cu113 which is incompatible.


In [1]:
from itertools import product
from itertools import combinations

from avalanche.benchmarks.classic import SplitMNIST
from avalanche.benchmarks.generators import dataset_benchmark


import torch
import torchvision
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
from torch.utils.tensorboard import SummaryWriter



import torch.nn.functional as F
from torcheval.metrics.functional import multiclass_confusion_matrix
from torch.optim import Adam
from torch.nn import CrossEntropyLoss

from torchvision.utils import save_image
from torchvision.transforms import ToTensor
from torchvision.datasets import ImageFolder
from torchvision import transforms

from itertools import product
from itertools import combinations


import matplotlib.pyplot as plt 
import seaborn as sns
from matplotlib.animation import FuncAnimation ,FFMpegWriter ,PillowWriter

import dill
import numpy as np
import os
import json
import pandas as pd
from tqdm import tqdm
import copy

In [2]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

In [3]:
#split_mnist = SplitMNIST(n_experiences=10)

In [4]:
'''for i in split_mnist.train_stream[0].dataset:
    print(i[0].shape)
    print(i[1])
    break
'''

'for i in split_mnist.train_stream[0].dataset:\n    print(i[0].shape)\n    print(i[1])\n    break\n'

In [5]:
#split_mnist.train_stream[0].dataset[0][1]

In [6]:
#import matplotlib.pyplot as plt
#plt.imshow(split_mnist.train_stream[0].dataset[0][0].numpy()[0], cmap='gray')

In [7]:
#len(split_mnist.train_stream)

### Data creation

In [ ]:
for k in range(10):
    if not(os.path.isdir(".//data//SplitMnist//train//")):
        os.mkdir(".//data//SplitMnist//train//")
    if not(os.path.isdir(".//data//SplitMnist//train//{}".format(k))):
        os.mkdir(".//data//SplitMnist//train//{}".format(k))
    if not(os.path.isdir(".//data//SplitMnist//test//")):
        os.mkdir(".//data//SplitMnist//test//")
    if not(os.path.isdir(".//data//SplitMnist//test//{}".format(k))):
        os.mkdir(".//data//SplitMnist//test//{}".format(k))
for i in tqdm(range(len(split_mnist.train_stream))):
    for j in range(len(split_mnist.train_stream[i].dataset)):
        save_image(split_mnist.train_stream[i].dataset[j][0], ".//data//SplitMnist//train//{}//{}.png".format(split_mnist.train_stream[i].dataset[j][1],j))
    #print("fold {}//{}//{}.png saved".format(j,L_labels1[img_idx],test_index[img_idx]))

In [ ]:
for i in tqdm(range(len(split_mnist.test_stream))):
    for j in range(len(split_mnist.test_stream[i].dataset)):
        save_image(split_mnist.test_stream[i].dataset[j][0], ".//data//SplitMnist//test//{}//{}.png".format(split_mnist.test_stream[i].dataset[j][1],j))

In [3]:
from torchvision import datasets
IMG_EXTENSIONS = ('.jpg', '.jpeg', '.png', '.ppm', '.bmp', '.pgm', '.tif', '.tiff', '.webp')

class ClassSpecificImageFolder(datasets.DatasetFolder):
    def __init__(
            self,
            root,
            dropped_classes=[],
            transform = None,
            target_transform = None,
            loader = datasets.folder.default_loader,
            is_valid_file = None,
    ):
        self.dropped_classes = dropped_classes
        super(ClassSpecificImageFolder, self).__init__(root, loader, IMG_EXTENSIONS if is_valid_file is None else None,
                                                       transform=transform,
                                                       target_transform=target_transform,
                                                       is_valid_file=is_valid_file)
        self.imgs = self.samples

    def find_classes(self, directory):
        classes = sorted(entry.name for entry in os.scandir(directory) if entry.is_dir())
        classes = [c for c in classes if c not in self.dropped_classes]
        if not classes:
            raise FileNotFoundError(f"Couldn't find any class folder in {directory}.")

        class_to_idx = {cls_name: i for i, cls_name in enumerate(classes)}
        return classes, class_to_idx

# Single experiences

In [49]:
#ListExperiences=list()
ListExperiences_=list()
All=list(range(10))
for sample in range(2,10,1):
    S=combinations(range(10), sample)
    #All=list(range(10))
    for i in S :
        L1=list(i)
        L2=[k for k in All if k not in L1] 
        ListExperiences_.append(L1)
len(ListExperiences_)

1012

In [54]:
L2_=[k for k in ListExperiences_ if k not in ListExperiences] 
print("Missing elements:", L2_)

Missing elements: [[0, 1, 2, 3, 4, 5, 6, 7, 8], [0, 1, 2, 3, 4, 5, 6, 7, 9], [0, 1, 2, 3, 4, 5, 6, 8, 9], [0, 1, 2, 3, 4, 5, 7, 8, 9], [0, 1, 2, 3, 4, 6, 7, 8, 9], [0, 1, 2, 3, 5, 6, 7, 8, 9], [0, 1, 2, 4, 5, 6, 7, 8, 9], [0, 1, 3, 4, 5, 6, 7, 8, 9], [0, 2, 3, 4, 5, 6, 7, 8, 9], [1, 2, 3, 4, 5, 6, 7, 8, 9]]


In [5]:
ListExperiences.append([x for x in range(10)])

# Pairs of experiences (with and without repetition)

In [6]:
Pairs_exp=list()

All=list(range(10))
for sample in range(2,9,1):
    S=combinations(range(10), sample)
    #All=list(range(10))
    for i in S :
        L1=list(i)
        L2=[k for k in All if k not in L1] 
        for sample2 in range(2,9,1):
            S2=combinations(L2, sample2)
            for j in S2:
                pair=[]
                pair.append(L1)
                sub=list(j)
                pair.append(sub)
                Pairs_exp.append(pair)
len(Pairs_exp)

46872

In [5]:
Pairs_exp=list()
All=list(range(10))
for sample in range(2,9,1):
    S=combinations(range(10), sample)
    #All=list(range(10))
    for i in S :
        L1=list(i)
        L2=[k for k in All if k not in L1] 
        for sample2 in range(2,9,1):
            S2=combinations(L2, sample2)
            for j in S2:
                pair=[]
                pair.append(L1)
                sub=list(j)
                pair.append(sub)
                pair.sort()
                if pair not in Pairs_exp :
                    Pairs_exp.append(pair)
len(Pairs_exp)             

23436

In [10]:
#Pairs_exp[0] ,Pairs_exp[10000],Pairs_exp[20000],Pairs_exp[30000],Pairs_exp[40000],Pairs_exp[46871]

In [11]:
ListExperiences[0] ,ListExperiences[1000]

([0, 1], [1, 3, 4, 5, 6, 7, 8, 9])

In [6]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")


class CNN(nn.Module):
    def __init__(
        self,
        channels_in,
        nlin="leakyrelu",
        dropout=0.0,
        init_type="uniform",
    ):
        super().__init__()
        # init module list
        self.module_list = nn.ModuleList()
        ### ASSUMES 28x28 image size
        ## compose layer 1
        self.module_list.append(nn.Conv2d(channels_in, 8, 5))
        self.module_list.append(nn.MaxPool2d(2, 2))
        self.module_list.append(self.get_nonlin(nlin))
        # apply dropout
        if dropout > 0:
            self.module_list.append(nn.Dropout(dropout))
        ## compose layer 2
        self.module_list.append(nn.Conv2d(8, 6, 5))
        self.module_list.append(nn.MaxPool2d(2, 2))
        self.module_list.append(self.get_nonlin(nlin))
        ## add dropout
        if dropout > 0:
            self.module_list.append(nn.Dropout(dropout))
        ## compose layer 3
        self.module_list.append(nn.Conv2d(6, 4, 2))
        self.module_list.append(self.get_nonlin(nlin))
        ## add flatten layer
        self.module_list.append(nn.Flatten())
        ## add linear layer 1
        self.module_list.append(nn.Linear(3 * 3 * 4, 20))
        self.module_list.append(self.get_nonlin(nlin))
        ## add dropout
        if dropout > 0:
            self.module_list.append(nn.Dropout(dropout))
        ## add linear layer 1
        self.module_list.append(nn.Linear(20, 10))

        ### initialize weights with se methods
        self.initialize_weights(init_type)

    def initialize_weights(self, init_type):
        # print("initialze model")
        for m in self.module_list:
            if type(m) == nn.Linear or type(m) == nn.Conv2d:
                if init_type == "xavier_uniform":
                    torch.nn.init.xavier_uniform_(m.weight)
                if init_type == "xavier_normal":
                    torch.nn.init.xavier_normal_(m.weight)
                if init_type == "uniform":
                    torch.nn.init.uniform_(m.weight)
                if init_type == "normal":
                    torch.nn.init.normal_(m.weight)
                if init_type == "kaiming_normal":
                    torch.nn.init.kaiming_normal_(m.weight)
                if init_type == "kaiming_uniform":
                    torch.nn.init.kaiming_uniform_(m.weight)
                # set bias to some small non-zero value
                m.bias.data.fill_(0.01)

    def get_nonlin(self, nlin):
        # apply nonlinearity
        if nlin == "leakyrelu":
            return nn.LeakyReLU()
        if nlin == "relu":
            return nn.ReLU()
        if nlin == "tanh":
            return nn.Tanh()
        if nlin == "sigmoid":
            return nn.Sigmoid()
        if nlin == "silu":
            return nn.SiLU()
        if nlin == "gelu":
            return nn.GELU()


    def forward(self, x):
        # forward prop through module_list
        for layer in self.module_list:
            x = layer(x)
        return x

    def forward_activations(self, x):
        # forward prop through module_list
        activations = []
        for layer in self.module_list:
            x = layer(x)
            if (
                isinstance(layer, nn.Tanh)
                or isinstance(layer, nn.Sigmoid)
                or isinstance(layer, nn.ReLU)
                or isinstance(layer, nn.LeakyReLU)
                or isinstance(layer, nn.SiLU)
                or isinstance(layer, nn.GELU)
                or isinstance(layer, ORU)
                or isinstance(layer, ERU)
            ):
                activations.append(x)
        return x, activations
def train(model, trainloader, optimizer, criterion,nb_classes):
    List_mx=[]
    model.train()
    #print('Training')
    train_running_loss = 0.0
    train_running_correct = 0
    counter = 0
    for i, data in enumerate(trainloader):
        counter += 1
        image, labels = data
        image = image.to(device)
        labels = labels.to(device)
        optimizer.zero_grad()
        # forward pass
        outputs = model(image)
        # calculate the loss
        loss = criterion(outputs, labels)
        train_running_loss += loss.item()
        # calculate the accuracy
        _, preds = torch.max(outputs.data, 1)
        train_running_correct += (preds == labels).sum().item()
        mx=multiclass_confusion_matrix(preds ,labels,nb_classes,normalize="pred")
        List_mx.append(mx)
        # backpropagation
        loss.backward()
        # update the optimizer parameters
        optimizer.step()
    
    # loss and accuracy for the complete epoch
    epoch_loss = train_running_loss / counter
    epoch_acc = 100. * (train_running_correct / len(trainloader.dataset))
    return epoch_loss, epoch_acc,List_mx


def validate(model, testloader, criterion,nb_classes):
    List_mx=[]
    model.eval()
    valid_running_loss = 0.0
    valid_running_correct = 0
    counter = 0
    with torch.no_grad():
        for i, data in enumerate(testloader):
            counter += 1
            
            image, labels = data
            image = image.to(device)
            labels = labels.to(device)
            # forward pass
            outputs = model(image)
            # calculate the loss
            loss = criterion(outputs, labels)
            valid_running_loss += loss.item()
            # calculate the accuracy
            _, preds = torch.max(outputs.data, 1)
            valid_running_correct += (preds == labels).sum().item()
            mx=multiclass_confusion_matrix(preds ,labels,nb_classes,normalize="pred")
            List_mx.append(mx)
        
    # loss and accuracy for the complete epoch
    epoch_loss = valid_running_loss / counter
    epoch_acc = 100. * (valid_running_correct / len(testloader.dataset))
    return epoch_loss, epoch_acc,List_mx
def create_frame(step,ax,data):
    ax=ax.cla()
    sns.heatmap(data[step][-1].cpu(),annot=True,cmap="cubehelix",ax=ax,cbar=False)
    plt.title('Epoch {} training {}'.format(step,exp)  )

In [7]:
ListExperiences[-1]

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9]

In [13]:
exper=os.listdir("checkpoints/")
missing=0
L_missing=[]
L_missingL=[]
for folder in exper:
    if len(os.listdir("checkpoints/{}".format(folder)))<3 and ("gelu" not in os.listdir("checkpoints/{}".format(folder))) :
        missing=missing+1
        L_missing.append(folder)
for folder in L_missing :       
    L_class=[]
    for classe in folder[1:-1].split(","):
        L_class.append(int(classe))
    L_missingL.append(L_class)           
len(L_missingL)

0

In [8]:
os.listdir("checkpoints/{}".format(folder))

NameError: name 'folder' is not defined

In [16]:
L_activations=["gelu","relu"]

In [10]:
train_loaders_paths=[ "./data/SplitMnist/train/{}".format(x) for x in range(10)]
test_loaders_paths=[ "./data/SplitMnist/test/{}".format(x) for x in range(10)]

In [ ]:
#train_loaders_paths=[ "./data/SplitMnist/train/{}".format(x) for x in range(10)]
#test_loaders_paths=[ "./data/SplitMnist/test/{}".format(x) for x in range(10)]


torch.manual_seed(887)
L_activations=["gelu"]#,"leakyrelu","sigmoid"]#,"relu","silu","tanh"]
L_inits=["kaiming_uniform"]



All=list(range(10))
patience=3
Margin=0.05
for i in range(len(L_activations)):
    for t,exp in enumerate(L2):
        L_train_acc=[]
        L_train_loss=[]
        L_test_acc_0=[]
        L_test_loss_0=[]
        
        L2=[k for k in All if k not in exp] 
        train_IF=ClassSpecificImageFolder( root="./data/SplitMnist/train/",dropped_classes=L2,transform=transforms.Compose([ transforms.ToTensor(),transforms.Grayscale(1)]))
        T_DL = DataLoader(dataset=train_IF, batch_size=90, num_workers=0, shuffle=True)
        test_IF=ClassSpecificImageFolder( root="./data/SplitMnist/test/",dropped_classes=L2,transform=transforms.Compose([ transforms.ToTensor(),transforms.Grayscale(1)]))
        Ts_DL = DataLoader(dataset=train_IF, batch_size=90, num_workers=0, shuffle=True)

        model = CNN(1,L_activations[i],0,L_inits[0])
        if not(os.path.isdir('./checkpoints/')):
            os.mkdir('./checkpoints/')
        if not(os.path.isdir('./checkpoints/{}/'.format(exp))):
            os.mkdir('./checkpoints/{}/'.format(exp))
        if not(os.path.isdir('./checkpoints/{}/{}'.format(exp,L_activations[i]))):
            os.mkdir('./checkpoints/{}/{}'.format(exp,L_activations[i]))
        if not(os.path.isdir('./checkpoints/{}/{}/metrics/'.format(exp,L_activations[i]))):
            os.mkdir('./checkpoints/{}/{}/metrics/'.format(exp,L_activations[i]))


        # lists to keep track of losses and accuracies
        train_loss, valid_loss_0 = [], [] 
        train_acc, valid_acc_0 = [], []
        train_confus,test_confus =[] , []
        Brain=copy.deepcopy(model)
        Brain=Brain.to(device)

        optimizer = Adam(Brain.parameters(), lr=0.05)
        scheduler = torch.optim.lr_scheduler.CyclicLR(optimizer, base_lr=1e-3, max_lr=0.1, step_size_up=1, mode="triangular2", cycle_momentum=False)

        criterion = CrossEntropyLoss()

        valid_epoch_loss0, valid_epoch_acc0,L_mx_st = validate(Brain, Ts_DL,criterion,10)
        valid_loss_0.append(valid_epoch_loss0)
        valid_acc_0.append(valid_epoch_acc0)
        test_confus.append(L_mx_st)
        #print(f"Validation loss: {valid_epoch_loss0:.3f}, validation acc 1: {valid_epoch_acc0:.3f}")

        #print('-'*50)
        # start the training
        stagnate=0
        for epoch in range(41):
            print(f"[INFO]: Epoch {epoch+1} of 40" , t ,L_activations[i])
            train_epoch_loss, train_epoch_acc ,L_mx = train(Brain, T_DL, optimizer, criterion,10)
            train_confus.append(L_mx)
            train_loss.append(train_epoch_loss)
            train_acc.append(train_epoch_acc)
            valid_epoch_loss0, valid_epoch_acc0,L_mx= validate(Brain, Ts_DL,  criterion,10)
            test_confus.append(L_mx)
            valid_loss_0.append(valid_epoch_loss0)
            valid_acc_0.append(valid_epoch_acc0)
            print(f"Training loss: {train_epoch_loss:.3f}, training acc: {train_epoch_acc:.3f}")
            print(f"Validation loss: {valid_epoch_loss0:.3f}, validation acc 1: {valid_epoch_acc0:.3f}")

            if (valid_epoch_acc0 >60) and (epoch >= 9):
                if epoch %5==1:
                    torch.save({'epoch': aux,'model_state_dict': Brain.state_dict(),'optimizer_state_dict': optimizer.state_dict(),},'./checkpoints/{}/{}/checkpoint epoch {}.pth'.format(exp,L_activations[i],epoch))
                if (abs(valid_epoch_acc0-valid_acc_0[-2])<=Margin)  :
                    print("stagnation")
                    stagnate=stagnate+1
                    if stagnate==patience :
                        epoch=-1
                    else:
                        continue
                else:
                    stagnate=0
                aux=epoch
                if (epoch==-1) :
                    aux=epoch
                    break
            print('-'*50)


        #torch.save(Brain.state_dict(),'./checkpoints/{}/{}/{}/checkpoint.pth'.format(ListExperiences[exp_idx][:5],activ,init))
        torch.save({'epoch': aux,'model_state_dict': Brain.state_dict(),'optimizer_state_dict': optimizer.state_dict(),},'./checkpoints/{}/{}/checkpoint epoch {}.pth'.format(exp,L_activations[i],epoch))
        L_train_acc.append(train_acc)
        L_train_loss.append(train_loss)
        L_test_acc_0.append(valid_acc_0)
        L_test_loss_0.append(valid_loss_0)

        direct='./checkpoints/{}/{}/metrics/'.format(exp,L_activations[i])
        M=np.array(L_test_acc_0) 
        np.save(direct+"Test Accuracy IID.npy", M)

        H=np.array(L_test_loss_0)
        np.save(direct+"Test Loss IID.npy",H)


        N=np.array(L_train_acc)
        np.save(direct+"Train Acc.npy",N)

        O=np.array(L_train_loss)
        np.save(direct+"Train Loss.npy",O)
        
        P=[train_confus[i][-1].cpu() for i in range(len(train_confus))]
        P=torch.stack(P)
        P=np.transpose(P, (1, 2, 0))
        np.save(direct+"multiclass train Confusion matrix raw.npy",P)
        
        W=[test_confus[i][-1].cpu() for i in range(len(test_confus))]
        W=torch.stack(W)
        W=np.transpose(W, (1, 2, 0))
        np.save(direct+"multiclass test Confusion matrix raw.npy",W)
        
        fig, ax = plt.subplots() 
        ax.cla()
        animation = FuncAnimation(fig, create_frame, frames=len(train_confus), fargs=(ax,train_confus))
        wr=PillowWriter(fps=1)
        animation.save('./checkpoints/{}/{}/metrics/Training mcx.gif'.format(exp,L_activations[i]) , writer=wr)
        fig, ax = plt.subplots() 
        ax.cla()
        animation = FuncAnimation(fig, create_frame, frames=len(test_confus), fargs=(ax,test_confus))
        wr=PillowWriter(fps=1)
        animation.save('./checkpoints/{}/{}/metrics/Testing mcx.gif'.format(exp,L_activations[i]) , writer=wr)


In [ ]:
#train_loaders_paths=[ "./data/SplitMnist/train/{}".format(x) for x in range(10)]
#test_loaders_paths=[ "./data/SplitMnist/test/{}".format(x) for x in range(10)]


torch.manual_seed(887)
L_activations=["silu","relu"]#,"leakyrelu","sigmoid"]#,"relu","silu","tanh"]
L_inits=["kaiming_uniform"]



All=list(range(10))
patience=3
Margin=0.05
for i in range(len(L_activations)):
    for t,exp in enumerate(L2_):
        L_train_acc=[]
        L_train_loss=[]
        L_test_acc_0=[]
        L_test_loss_0=[]
        
        L2=[k for k in All if k not in exp] 
        train_IF=ClassSpecificImageFolder( root="./data/SplitMnist/train/",dropped_classes=L2,transform=transforms.Compose([ transforms.ToTensor(),transforms.Grayscale(1)]))
        T_DL = DataLoader(dataset=train_IF, batch_size=90, num_workers=0, shuffle=True)
        test_IF=ClassSpecificImageFolder( root="./data/SplitMnist/test/",dropped_classes=L2,transform=transforms.Compose([ transforms.ToTensor(),transforms.Grayscale(1)]))
        Ts_DL = DataLoader(dataset=train_IF, batch_size=90, num_workers=0, shuffle=True)

        model = CNN(1,L_activations[i],0,L_inits[0])
        if not(os.path.isdir('./checkpoints/')):
            os.mkdir('./checkpoints/')
        if not(os.path.isdir('./checkpoints/{}/'.format(exp))):
            os.mkdir('./checkpoints/{}/'.format(exp))
        if not(os.path.isdir('./checkpoints/{}/{}'.format(exp,L_activations[i]))):
            os.mkdir('./checkpoints/{}/{}'.format(exp,L_activations[i]))
        if not(os.path.isdir('./checkpoints/{}/{}/metrics/'.format(exp,L_activations[i]))):
            os.mkdir('./checkpoints/{}/{}/metrics/'.format(exp,L_activations[i]))


        # lists to keep track of losses and accuracies
        train_loss, valid_loss_0 = [], [] 
        train_acc, valid_acc_0 = [], []
        train_confus,test_confus =[] , []
        Brain=copy.deepcopy(model)
        Brain=Brain.to(device)

        optimizer = Adam(Brain.parameters(), lr=0.05)
        scheduler = torch.optim.lr_scheduler.CyclicLR(optimizer, base_lr=1e-3, max_lr=0.1, step_size_up=1, mode="triangular2", cycle_momentum=False)

        criterion = CrossEntropyLoss()

        valid_epoch_loss0, valid_epoch_acc0,L_mx_st = validate(Brain, Ts_DL,criterion,10)
        valid_loss_0.append(valid_epoch_loss0)
        valid_acc_0.append(valid_epoch_acc0)
        test_confus.append(L_mx_st)
        #print(f"Validation loss: {valid_epoch_loss0:.3f}, validation acc 1: {valid_epoch_acc0:.3f}")

        #print('-'*50)
        # start the training
        stagnate=0
        for epoch in range(41):
            print(f"[INFO]: Epoch {epoch+1} of 40" , t ,L_activations[i])
            train_epoch_loss, train_epoch_acc ,L_mx = train(Brain, T_DL, optimizer, criterion,10)
            train_confus.append(L_mx)
            train_loss.append(train_epoch_loss)
            train_acc.append(train_epoch_acc)
            valid_epoch_loss0, valid_epoch_acc0,L_mx= validate(Brain, Ts_DL,  criterion,10)
            test_confus.append(L_mx)
            valid_loss_0.append(valid_epoch_loss0)
            valid_acc_0.append(valid_epoch_acc0)
            print(f"Training loss: {train_epoch_loss:.3f}, training acc: {train_epoch_acc:.3f}")
            print(f"Validation loss: {valid_epoch_loss0:.3f}, validation acc 1: {valid_epoch_acc0:.3f}")

            if (valid_epoch_acc0 >60) and (epoch >= 9):
                if epoch %5==1:
                    torch.save({'epoch': aux,'model_state_dict': Brain.state_dict(),'optimizer_state_dict': optimizer.state_dict(),},'./checkpoints/{}/{}/checkpoint epoch {}.pth'.format(exp,L_activations[i],epoch))
                if (abs(valid_epoch_acc0-valid_acc_0[-2])<=Margin)  :
                    print("stagnation")
                    stagnate=stagnate+1
                    if stagnate==patience :
                        epoch=-1
                    else:
                        continue
                else:
                    stagnate=0
                aux=epoch
                if (epoch==-1) :
                    aux=epoch
                    break
            print('-'*50)


        #torch.save(Brain.state_dict(),'./checkpoints/{}/{}/{}/checkpoint.pth'.format(ListExperiences[exp_idx][:5],activ,init))
        torch.save({'epoch': aux,'model_state_dict': Brain.state_dict(),'optimizer_state_dict': optimizer.state_dict(),},'./checkpoints/{}/{}/checkpoint.pth'.format(exp,L_activations[i],epoch))
        L_train_acc.append(train_acc)
        L_train_loss.append(train_loss)
        L_test_acc_0.append(valid_acc_0)
        L_test_loss_0.append(valid_loss_0)

        direct='./checkpoints/{}/{}/metrics/'.format(exp,L_activations[i])
        M=np.array(L_test_acc_0) 
        np.save(direct+"Test Accuracy IID.npy", M)

        H=np.array(L_test_loss_0)
        np.save(direct+"Test Loss IID.npy",H)


        N=np.array(L_train_acc)
        np.save(direct+"Train Acc.npy",N)

        O=np.array(L_train_loss)
        np.save(direct+"Train Loss.npy",O)
        
        P=[train_confus[i][-1].cpu() for i in range(len(train_confus))]
        P=torch.stack(P)
        P=np.transpose(P, (1, 2, 0))
        np.save(direct+"multiclass train Confusion matrix raw.npy",P)
        
        W=[test_confus[i][-1].cpu() for i in range(len(test_confus))]
        W=torch.stack(W)
        W=np.transpose(W, (1, 2, 0))
        np.save(direct+"multiclass test Confusion matrix raw.npy",W)
        
        fig, ax = plt.subplots() 
        ax.cla()
        animation = FuncAnimation(fig, create_frame, frames=len(train_confus), fargs=(ax,train_confus))
        wr=PillowWriter(fps=1)
        animation.save('./checkpoints/{}/{}/metrics/Training mcx.gif'.format(exp,L_activations[i]) , writer=wr)
        fig, ax = plt.subplots() 
        ax.cla()
        animation = FuncAnimation(fig, create_frame, frames=len(test_confus), fargs=(ax,test_confus))
        wr=PillowWriter(fps=1)
        animation.save('./checkpoints/{}/{}/metrics/Testing mcx.gif'.format(exp,L_activations[i]) , writer=wr)


[INFO]: Epoch 1 of 40 0 silu
Training loss: 0.546, training acc: 82.528
Validation loss: 0.206, validation acc 1: 93.658
--------------------------------------------------
[INFO]: Epoch 2 of 40 0 silu
Training loss: 0.171, training acc: 94.843
Validation loss: 0.137, validation acc 1: 95.740
--------------------------------------------------
[INFO]: Epoch 3 of 40 0 silu
Training loss: 0.131, training acc: 95.985
Validation loss: 0.122, validation acc 1: 96.252
--------------------------------------------------
[INFO]: Epoch 4 of 40 0 silu
Training loss: 0.110, training acc: 96.670
Validation loss: 0.102, validation acc 1: 96.813
--------------------------------------------------
[INFO]: Epoch 5 of 40 0 silu
Training loss: 0.099, training acc: 96.990
Validation loss: 0.090, validation acc 1: 97.158
--------------------------------------------------
[INFO]: Epoch 6 of 40 0 silu
Training loss: 0.090, training acc: 97.213
Validation loss: 0.080, validation acc 1: 97.483
-------------------

### Access weights

In [ ]:
ListModelvec=[]
check=torch.load(f".//checkpoints//{ListExperiences[exp][:5]}//{L_activations[activ]}//{L_inits[init]}//checkpoint.pth",pickle_module=dill,map_location=device)
model = CNN(1,activ,0,init)
model=model.to(device)
model.load_state_dict(check["model_state_dict"])
L_param=[]
for param in model.parameters():
    m = nn.Flatten(0,-1)
    L_param.append(m(param))
vec = torch.Tensor()
vec=vec.to(device)
for idx in L_param:
    vec = torch.cat((vec, idx.view(-1)))
print(vec.shape)
ListModelvec.append(vec)

In [43]:
acc=np.load(f".//checkpoints//{ListExperiences[0]}//silu//metrics//Test Accuracy IID.npy")
acc[0][11+1]

98.29166666666667

In [35]:
L_activations=["gelu"]#,"leakyrelu","sigmoid"]#,"relu","gelu","tanh"]
L_inits=["kaiming_uniform"]

Cols=["label"]+[x for x in range(10)]+["Activation"]+["weight {}".format(x) for x in range(200)]+["bias {}".format(x) for x in range(200,208)]+["weight {}".format(x) for x in range(208,1408)]+["bias {}".format(x) for x in range(1408,1414)]+["weight {}".format(x) for x in range(1414,1510)]+["bias {}".format(x) for x in range(1510,1514)]+["weight {}".format(x) for x in range(1514,2234)]+["bias {}".format(x) for x in range(2234,2254)]+["weight {}".format(x) for x in range(2254,2454)]+["bias {}".format(x) for x in range(2454,2464)]+["Accuracy"]
check_name=[' epoch 11',' epoch 16',' epoch 21',' epoch 26',' epoch 31',' epoch 36','']# 
Weights= pd.DataFrame(columns=Cols)

All=list(range(10))

for name in check_name:
    Weights= pd.DataFrame(columns=Cols)
    for exp in tqdm(ListExperiences) :
        try:
            row=[]

            row.append(exp)
            for label in All:
                if label in exp:
                    row.append(1)
                else:
                    row.append(0)

            row.append(L_activations[0])

            check=torch.load(f".//checkpoints//{exp}//relu//checkpoint{name}.pth",pickle_module=dill,map_location=device)
            model = CNN(1,L_activations[0],0,L_inits[0])
            model=model.to(device)
            model.load_state_dict(check["model_state_dict"])
            L_param=[]
            for param in model.parameters():
                m = nn.Flatten(0,-1)
                L_param.append(m(param))
            vec = torch.Tensor()
            vec=vec.to(device)
            for idx in L_param:
                vec = torch.cat((vec, idx.view(-1)))
            vec=vec.detach().cpu().numpy()
            row.extend(vec)

            acc=np.load(f".//checkpoints//{exp}//{L_activations[0]}//metrics//Test Accuracy IID.npy")
            if name != '':
                row.append(acc[0][int(name[-2:])+1])
            else:
                row.append(acc[0][-1])
            Weights.loc[len(Weights)]=row
        except:
            continue
    print(Weights.head(2).style.set_properties(subset=['Activation'], **{'width': '300px'}))
    Weights.to_csv(f"Weights {L_activations[0]}{name}.csv", index=False)

100%|██████████| 1003/1003 [01:57<00:00,  8.55it/s]


100%|██████████| 1003/1003 [01:52<00:00,  8.93it/s]


100%|██████████| 1003/1003 [01:42<00:00,  9.78it/s]


100%|██████████| 1003/1003 [01:29<00:00, 11.17it/s]


100%|██████████| 1003/1003 [01:18<00:00, 12.72it/s]


100%|██████████| 1003/1003 [01:08<00:00, 14.59it/s]


100%|██████████| 1003/1003 [01:57<00:00,  8.50it/s]


## Create train , validation , test loaders 

In [7]:
df_sil=pd.read_csv("Weights silu epoch 11.csv")
print(len(df_sil))
param_columns=df_sil.columns[12:-1]
l=[0,1]
df_sil[df_sil['label']=='{}'.format([0,1])]

1003


label  0  1  2  3  4  5  6  7  8  ...  bias 2455 bias 2456  bias 2457  \
0  [0, 1]  1  1  0  0  0  0  0  0  0  ...   0.303834 -0.083217  -0.176684   

   bias 2458  bias 2459  bias 2460  bias 2461  bias 2462  bias 2463   Accuracy  
0   -0.09376   0.162325  -0.027736   0.251412  -0.166753  -0.106637  98.291667  

[1 rows x 2477 columns]

In [8]:
df_gel=pd.read_csv("Weights gelu epoch 11.csv")
print(len(df_gel))
param_columns=df_gel.columns[12:-1]
l=[0,1]
df_gel[df_gel['label']=='{}'.format([0,1])]

1003


label  0  1  2  3  4  5  6  7  8  ...  bias 2455 bias 2456  bias 2457  \
0  [0, 1]  1  1  0  0  0  0  0  0  0  ...   0.303834 -0.083217  -0.176684   

   bias 2458  bias 2459  bias 2460  bias 2461  bias 2462  bias 2463   Accuracy  
0   -0.09376   0.162325  -0.027736   0.251412  -0.166753  -0.106637  98.146667  

[1 rows x 2477 columns]

In [38]:
listed=list(df_gel['label'].values)
alll=[f'{x}' for x in ListExperiences ]
missing_elements = set(alll) - set(listed)

print("Missing elements:", list(missing_elements))

Missing elements: []


In [33]:
import ast

# Assuming s is the string created using f{}.format(L)
s = list(missing_elements)[0]

# Use ast.literal_eval to safely convert the string to a list
L = ast.literal_eval(s)
L_missing_elements=[ ast.literal_eval(list(missing_elements)[i]) for i in range(len(missing_elements)) ]
print(L_missing_elements)


[[2, 3, 4, 7, 9], [0, 1, 4, 5, 9]]


In [9]:
df_rel=pd.read_csv("Weights relu epoch 11.csv")

print(len(df_rel))
l=[0,1]
df_rel[df_rel['label']=='{}'.format([0,1])]

1003


label  0  1  2  3  4  5  6  7  8  ...  bias 2455 bias 2456  bias 2457  \
0  [0, 1]  1  1  0  0  0  0  0  0  0  ...   0.303834 -0.083217  -0.176684   

   bias 2458  bias 2459  bias 2460  bias 2461  bias 2462  bias 2463   Accuracy  
0   -0.09376   0.162325  -0.027736   0.251412  -0.166753  -0.106637  98.036667  

[1 rows x 2477 columns]

In [10]:
df=pd.concat([df_gel, df_rel, df_sil], ignore_index=True)
#df.tail().style.set_properties(subset=['Activation'], **{'width': '300px'})

In [11]:

from sklearn.preprocessing import LabelEncoder, OneHotEncoder

# Suppose 'string_feature' is the name of the string feature column in your DataFrame
string_feature = df['Activation']

# Label Encoding
label_encoder = LabelEncoder()
numeric_labels = label_encoder.fit_transform(list(df[df.columns[11]]))
numeric_labels

array([0, 0, 0, ..., 2, 2, 2])

In [12]:
onehot_encoder = OneHotEncoder(sparse=False)
onehot_encoded = onehot_encoder.fit_transform(numeric_labels.reshape(-1, 1))

# Replace the original string feature with the numeric or one-hot encoded features
df = pd.concat([df.drop('Activation', axis=1), pd.DataFrame(onehot_encoded)], axis=1)
df.head().style.set_properties(subset=list(df.columns[11:15]), **{'width': '300px'})

In [13]:
df=df.rename(columns={0: "gelu", 1: "relu", 2: "silu"}, errors="raise") 
df.head().style.set_properties(subset=list(df.columns[11:15]), **{'width': '300px'})

In [16]:
column_to_move = 'silu'
desired_index = 13  # Set the desired index where you want to move the column

# Pop the column from its current position
column = df.pop(column_to_move)

# Insert the column at the desired index
df.insert(desired_index, column_to_move, column)
df.head().style.set_properties(subset=list(df.columns[11:15]), **{'width': '300px'})

/tmp/ipykernel_418123/3183181590.py:8: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df.insert(desired_index, column_to_move, column)


In [47]:
#df.tail().style.set_properties(subset=list(df.columns[11:15]), **{'width': '300px'})

In [17]:
params_cols=list(df.columns[11:-1])
params_cols[:10]

['gelu',
 'relu',
 'silu',
 'weight 0',
 'weight 1',
 'weight 2',
 'weight 3',
 'weight 4',
 'weight 5',
 'weight 6']

In [18]:
Pairs_exp=list()
All=list(range(10))
for sample in range(2,9,1):
    S=combinations(range(10), sample)
    #All=list(range(10))
    for i in S :
        L1=list(i)
        L2=[k for k in All if k not in L1] 
        for sample2 in range(2,9,1):
            S2=combinations(L2, sample2)
            for j in S2:
                pair=[]
                pair.append(L1)
                sub=list(j)
                pair.append(sub)
                pair.sort()
                if pair not in Pairs_exp :
                    Pairs_exp.append(pair)
len(Pairs_exp)             

23436

In [19]:
train_pair=[]
train_tgt=[]

val_pair=[]
val_tgt=[]

test_pair=[]
test_tgt=[]
for pair in tqdm(Pairs_exp):
    if (len(pair[0])==5 and len(pair[1])==5) or(len(pair[0])==4 and len(pair[1])==4) or(len(pair[0])==3 and len(pair[1])==3) or (len(pair[0])==2 and len(pair[1])==2):
        test_pair.append(pair)
        tg=(pair[0]+pair[1]).sort()
        test_tgt.append(tg)
    elif (len(pair[0])==7 and len(pair[1])==2) or (len(pair[0])==2 and len(pair[1])==7) or (len(pair[0])==6 and len(pair[1])==3) or (len(pair[0])==3 and len(pair[1])==6) or (len(pair[0])==4 and len(pair[1])==5) or (len(pair[0])==5 and len(pair[1])==4):
        val_pair.append(pair)
        tg=(pair[0]+pair[1]).sort()
        val_tgt.append(tg)
    else :
        train_pair.append(pair)
        tg=(pair[0]+pair[1]).sort()
        train_tgt.append(tg)

100%|██████████| 23436/23436 [00:00<00:00, 552622.40it/s]


In [20]:
len(test_pair),len(train_pair),len(val_pair),len(test_tgt),len(train_tgt),len(val_tgt)

(4431, 16545, 2460, 4431, 16545, 2460)

In [52]:
df[df['label']=='{}'.format([0,1])].style.set_properties( **{'width': '300px'})

In [92]:
df.to_csv("zoo.csv",index=False, header=True)

In [54]:
df[df['label']=='{}'.format([0,1])]['gelu']

0       1.0
1003    0.0
2006    0.0
Name: gelu, dtype: float64

In [27]:
torch.from_numpy(df[df['label']=='{}'.format([0,1])][params_cols].to_numpy().astype('float64') )

tensor([[ 1.0000,  0.0000,  0.0000,  ...,  0.2514, -0.1668, -0.1066],
        [ 0.0000,  1.0000,  0.0000,  ...,  0.2514, -0.1668, -0.1066],
        [ 0.0000,  0.0000,  1.0000,  ...,  0.2514, -0.1668, -0.1066]],
       dtype=torch.float64)

In [56]:
#train_pair[0]

[[0, 1], [2, 3, 4]]

In [83]:
#torch.from_numpy(df[(df['label']=='{}'.format(pair[0])) & (df['gelu']==1) ][params_cols].to_numpy().astype('float64'))

tensor([[ 1.0000,  0.0000,  0.0000,  ...,  0.2514, -0.1668, -0.1066]],
       dtype=torch.float64)

In [41]:
torch.from_numpy(df[ (df['label']=='{}'.format([0, 1, 2, 3, 4, 5, 6, 7, 8])) & (df['gelu']==float(1) )][params_cols].to_numpy().astype('float64'))

tensor([], size=(0, 2467), dtype=torch.float64)

In [39]:
L_Stream1=[]
L_Stream2=[]
tgt=[]
for c,pair in enumerate(val_pair):
    L_Stream1.append(torch.from_numpy(df[(df['label']=='{}'.format(pair[0])) & (df['gelu']==float(1)) ][params_cols].to_numpy().astype('float64')))
    L_Stream2.append(torch.from_numpy(df[(df['label']=='{}'.format(pair[0])) & (df['gelu']==float(1)) ][params_cols].to_numpy().astype('float64')))
    tg=pair[0]+pair[1]
    tg.sort()
    print(tg)
    tgt.append(torch.from_numpy(df[ (df['label']=='{}'.format(tg)) & (df['gelu']==float(1) )][params_cols].to_numpy().astype('float64')))
    break
    L_Stream1.append(torch.from_numpy(df[(df['label']=='{}'.format(pair[0])) & (df['relu']==float(1)) ][params_cols].to_numpy().astype('float64')))
    L_Stream2.append(torch.from_numpy(df[(df['label']=='{}'.format(pair[0])) & (df['relu']==float(1)) ][params_cols].to_numpy().astype('float64')))
    tg=pair[0]+pair[1]
    tg.sort()
    #print(tg)
    tgt.append(torch.from_numpy(df[ (df['label']=='{}'.format(tg)) & (df['relu']==float(1) )][params_cols].to_numpy().astype('float64')))
    
    L_Stream1.append(torch.from_numpy(df[(df['label']=='{}'.format(pair[0])) & (df['silu']==float(1)) ][params_cols].to_numpy().astype('float64')))
    L_Stream2.append(torch.from_numpy(df[(df['label']=='{}'.format(pair[0])) & (df['silu']==float(1)) ][params_cols].to_numpy().astype('float64')))
    tg=pair[0]+pair[1]
    tg.sort()
    #print(tg)
    tgt.append(torch.from_numpy(df[ (df['label']=='{}'.format(tg)) & (df['silu']==float(1) )][params_cols].to_numpy().astype('float64')))
    
Stream1=torch.stack(L_Stream1)
Stream2=torch.stack(L_Stream2)
target=torch.stack(tgt)

[0, 1, 2, 3, 4, 5, 6, 7, 8]


In [37]:
df.head().style.set_properties(**{'width': '300px'})

In [40]:
tgt

[tensor([], size=(0, 2467), dtype=torch.float64)]

In [22]:
Stream1=torch.reshape(Stream1, (Stream1.shape[0], Stream1.shape[2]))
Stream2=torch.reshape(Stream2, (Stream2.shape[0], Stream2.shape[2]))
target=torch.reshape(target, (target.shape[0], target.shape[2]))
Stream1.shape,Stream2.shape,target.shape

RuntimeError: shape '[7380, 2467]' is invalid for input of size 0

In [91]:
from torch.utils.data import TensorDataset
train_dataset = TensorDataset(Stream1,Stream2, target)
torch.save(train_dataset, 'train_dataset.pt')

In [189]:
dsab_cat_loader = DataLoader(train_dataset)

In [190]:
for x1,x2,tg in dsab_cat_loader:
    print(x1.shape,x2.shape,tg.shape)
    break

torch.Size([1, 1, 2464]) torch.Size([1, 1, 2464]) torch.Size([1, 0, 2464])


## reconstruct Checkpoint

In [ ]:
from collections import OrderedDict
import copy
import numpy as np

for class_order_idx in range(len(ListExperiences)):
    for i in product(L_activations,L_inits):
        checkpoint=OrderedDict()
        vector_aux= copy.deepcopy(y)
        vector_aux=vector_aux.cpu()
        checkpoint["module_list.0.weight"]=torch.tensor(np.array(vector_aux[l][0:200]).reshape([8, 1, 5, 5]))
        checkpoint["module_list.0.bias"]=torch.tensor(np.array(vector_aux[l][200:208]).reshape([8]))
        checkpoint["module_list.3.weight"]=torch.tensor(np.array(vector_aux[l][208:1408]).reshape([6, 8, 5, 5]))
        checkpoint["module_list.3.bias"]=torch.tensor(np.array(vector_aux[l][1408:1414]).reshape([6]))
        checkpoint["module_list.6.weight"]=torch.tensor(np.array(vector_aux[l][1414:1510]).reshape([4, 6, 2, 2]))
        checkpoint["module_list.6.bias"]=torch.tensor(np.array(vector_aux[l][1510:1514]).reshape([4]))
        checkpoint["module_list.9.weight"]=torch.tensor(np.array(vector_aux[l][1514:2234]).reshape([20,36]))
        checkpoint["module_list.9.bias"]=torch.tensor(np.array(vector_aux[l][2234:2254]).reshape([20]))
        checkpoint["module_list.11.weight"]=torch.tensor(np.array(vector_aux[l][2254:2454]).reshape([10,20]))
        checkpoint["module_list.11.bias"]=torch.tensor(np.array(vector_aux[l][2454:2464]).reshape([10]))
        model = CNN(1,list(i)[0],0,list(i)[1]) ####
        model.load_state_dict(checkpoint)
        model.eval()
        torch.save(model.state_dict(), './checkpoints/Cumulative/{}/{}/{}/1/Reconsturcted checkpoint.pth'.format(ListExperiences[class_order_idx][:5],list(i)[0],list(i)[1]))